In [1]:
#import tuxml
import pandas as pd 
import warnings
warnings.filterwarnings('ignore')

#df = tuxml.load_dataset()
# path = r"x264/sampledConfigurations_distBased_t3.csv"
#path = r"sampledConfigurations_distBased_t3.csv"
samples_config = ['distBased', 'divDistBased','henard', 'random', 'solverBased', 'twise']

# for config_name in samples_config:
#     path = r"sampledConfigurations_"+config_name+"_t3.csv"
# #     df.append(pd.read_csv(path, sep=';'))
#     display(path)

# df = pd.read_csv(path, sep=';')


In [2]:
# df_importance = pd.read_csv("feature_importanceRF.csv")
# df_importance = df[df_importance[:100]["Unnamed: 0"].values]
# df_importance.head()

In [2]:
#size_methods = ["vmlinux", "GZIP-bzImage", "GZIP-vmlinux", "GZIP", "BZIP2-bzImage", 
#              "BZIP2-vmlinux", "BZIP2", "LZMA-bzImage", "LZMA-vmlinux", "LZMA", "XZ-bzImage", "XZ-vmlinux", "XZ", 
#?              "LZO-bzImage", "LZO-vmlinux", "LZO", "LZ4-bzImage", "LZ4-vmlinux", "LZ4"]

size_methods = ["Performance"]
#additional_ft = ["nbyes", "nbno", "nbmodule", "nbyesmodule"]

In [3]:
def features_engine(df):
    
    engine_values = []
    for i, j in df.iterrows():
        num1s = 0
        num1s = j.value_counts()[1]
        engine_values.append(num1s)
    
    df['construction'] = engine_values
    

In [4]:
path = r"sampledConfigurations_distBased_t3.csv"
df = pd.read_csv(path, sep=';')
features_engine(df)
display(df)

root  HAVE_CRYPTO  HAVE_HASH  HAVE_REPLICATION  HAVE_VERIFY  \
0       1            0          0                 0            0   
1       1            1          1                 1            1   
2       1            1          1                 1            1   
3       1            0          0                 0            0   
4       1            1          0                 0            0   
..    ...          ...        ...               ...          ...   
358     1            1          0                 0            0   
359     1            0          1                 1            0   
360     1            1          1                 0            0   
361     1            1          0                 1            0   
362     1            1          1                 1            1   

     HAVE_SEQUENCE  HAVE_STATISTICS  DIAGNOSTIC  PAGESIZE  PS1K  ...  PS8K  \
0                0                0           0         1     1  ...     0   
1                1                0           1         1     0  ...     0   
2                1                1           1         1     0  ...     0   
3                0                0           0         1     0  ...     1   
4                0                0           0         1     0  ...     1   
..             ...              ...         ...       ...   ...  ...   ...   
358              0                1           0         1     0  ...     0   
359              1                0           0         1     0  ...     0   
360              1                0           0         1     0  ...     0   
361              1                0           0         1     0  ...     0   
362              1                0           0         1     0  ...     0   

     PS16K  PS32K  CACHESIZE  CS32MB  CS16MB  CS64MB  CS512MB  Performance  \
0        0      0          1       1       0       0        0     0.502896   
1        0      0          1       1       0       0        0     5.844917   
2        0      0          1       1       0       0        0     5.845517   
3        0      0          1       0       0       0        1     0.478544   
4        0      0          1       0       0       0        1    10.756226   
..     ...    ...        ...     ...     ...     ...      ...          ...   
358      0      0          1       1       0       0        0     6.522959   
359      0      0          1       1       0       0        0     0.504072   
360      0      0          1       1       0       0        0     5.830595   
361      0      0          1       1       0       0        0     6.515990   
362      0      0          1       1       0       0        0     5.816971   

     construction  
0               5  
1              11  
2              12  
3               5  
4               6  
..            ...  
358             7  
359             8  
360             8  
361             8  
362            10  

[363 rows x 21 columns]

In [5]:
#learning a model by using linear regression
import numpy as np
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn import linear_model
from sklearn.linear_model import ElasticNet

def run_regressorML(reg, test_size, size_target, x_train, x_test):
    assert(size_target in size_methods)
    reg.fit(x_train, y_train)
    y_pred = reg.predict(x_test)
    #y_pred = reg.intercept_ + np.sum(reg.coef_ * x_test.values, axis=1)
    dfErrors = pd.DataFrame({'Actual':y_test, 'Predicted':y_pred, "error":(y_pred - y_test).abs(), "% error":((y_pred - y_test)/y_test).abs()*100})
    return dfErrors["% error"].describe()

In [6]:
def ft_importances(coef_, col):
    importanceSeries = pd.Series(coef_, index=col.values)
    return importanceSeries[importanceSeries != 0].abs().sort_values(ascending = False)

In [7]:
df_result  = pd.DataFrame(columns = ['algorithm_name', 'ft_dummyfication', 'origin_ft_selection', 'ft_selection', 'hyperparameters', 'size_target', 'test_size', 'coef_order', 'accuracy'])
#df_result  = pd.DataFrame(columns = ['algorithm_name', 'hyperparameters', 'size_target', 'additional_ft', 'test_size', 'coef_order', 'accuracy'])

In [8]:
df_result

Empty DataFrame
Columns: [algorithm_name, ft_dummyfication, origin_ft_selection, ft_selection, hyperparameters, size_target, test_size, coef_order, accuracy]
Index: []

In [9]:
from sklearn.model_selection import GridSearchCV
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import ElasticNet
from sklearn import linear_model
from sklearn import metrics

ft_importance_enable = True
# def runFeatureSelection(df, config_name, num_features): 
for config_name in samples_config:
    for samplePerc in [0.3,0.4,0.5,0.6]:
        for t in [1,2,3]:
            
            path_name = config_name+"_t"+str(t)
            path = r"sampledConfigurations_"+path_name+".csv"
            
            df = pd.read_csv(path, sep=';')
            num_features = round(samplePerc*len(df.columns))

            df_importance = pd.read_csv("feature_importance_"+path_name+".csv")
            df_importance = df[df_importance[:num_features]["Unnamed: 0"].values]
            
            print("DF with Feature Importance")
            print("Sample features number: "+ str(num_features))
            display(df_importance)
            df_importance.head()

            target = "Performance"
            paramsLasso = {'alpha': [25,10,4,2,1.0,0.8,0.5,0.3,0.2,0.1,0.05,0.02,0.01],
                           'max_iter': [1, 5, 10, 100, 1000],}
            paramsRidge = {'alpha': [25,10,4,2,1.0,0.8,0.5,0.3,0.2,0.1,0.05,0.02,0.01]}
            paramsENet = {'alpha': [25,10,4,2,1.0,0.8,0.5,0.3,0.2,0.1,0.05,0.02,0.01],
                          'l1_ratio': [0.0, 0.5, 1.0, 0.1],
                          'max_iter': [1, 5, 10, 100, 1000],}

            for ft_dummyfication in [False, True]:
                if ft_dummyfication:
                    #Creating dummy variables in pandas
                    df = pd.get_dummies(df, columns=list(df.drop(columns=size_methods).columns.values))
#                     df_importance = pd.get_dummies(df_importance, columns=list(df_importance.drop(columns=size_methods).columns.values))
                    df_importance = pd.get_dummies(df_importance, columns=list(df_importance.columns.values))

                if ft_importance_enable:
                    ft_selection =  {'None': df.drop(columns=size_methods).columns,
                                'RandomForest': df_importance.columns[:num_features],}
                    
                else:
                    ft_selection =  {'None': df.drop(columns=size_methods).columns,
                                     'RandomForest': df.columns[:num_features],}

                for origin_ft_selection in ft_selection:
                    for size in [0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9]:

                        x_train, x_test, y_train, y_test = train_test_split(df[ft_selection[origin_ft_selection]], df[target], test_size=size, random_state=42)  
                        x_train, y_train = np.array(x_train.values), np.array(y_train.values)
                        
                        print(x_train)
                        print(y_train)
                        
                        if len(x_train) > 3:

                            model = {'LinearRegression': LinearRegression(),
                                     'Lasso': GridSearchCV(linear_model.Lasso(), param_grid=paramsLasso, cv=3).fit(x_train, y_train).best_estimator_,
                                     'Ridge': GridSearchCV(linear_model.Ridge(), param_grid=paramsRidge, cv=3).fit(x_train, y_train).best_estimator_,
                                     'ElasticNet': GridSearchCV(ElasticNet(), param_grid=paramsENet, scoring='r2', cv=3).fit(x_train, y_train).best_estimator_,
                                     'PolynomialRegression': LinearRegression()}
                        else:
                            if len(x_train) >= 2:
                                model = {'LinearRegression': LinearRegression(),
                                         'Lasso': GridSearchCV(linear_model.Lasso(), param_grid=paramsLasso, cv=2).fit(x_train, y_train).best_estimator_,
                                         'Ridge': GridSearchCV(linear_model.Ridge(), param_grid=paramsRidge, cv=2).fit(x_train, y_train).best_estimator_,
                                         'ElasticNet': GridSearchCV(ElasticNet(), param_grid=paramsENet, scoring='r2', cv=2).fit(x_train, y_train).best_estimator_,
                                         'PolynomialRegression': LinearRegression()}
                        for key in model:
                            if (key == 'PolynomialRegression') and (origin_ft_selection == 'None'):
                                print("It doesn't scale")
                            else:
                                if (key == 'PolynomialRegression'):
                                    #for 2 options we have: 𝑓(𝑥₁, 𝑥₂) = 𝑏₀ + 𝑏₁𝑥₁ + 𝑏₂𝑥₂ + 𝑏₃𝑥₁² + 𝑏₄𝑥₁𝑥₂ + 𝑏₅𝑥₂²
                                    x_train = PolynomialFeatures(degree=2, include_bias=False).fit_transform(x_train)
                                    x_test = PolynomialFeatures(degree=2, include_bias=False).fit_transform(x_test)

                                res_model = run_regressorML(model[key], test_size=size, size_target=target, x_train=x_train, x_test=x_test)

                                if (key == 'PolynomialRegression'):
                                    model[key].coef_ = model[key].coef_[:num_features]

#                                 print(model[key].coef_)
                                coef_order = ft_importances(model[key].coef_, col=ft_selection[origin_ft_selection])
                                df_result.loc[len(df_result)] = [key, ft_dummyfication, origin_ft_selection, ft_selection[origin_ft_selection], model[key], target, size, coef_order, res_model]
            display(df_result)
            if ft_importance_enable:
                df_result.to_csv("results_with_feature_importance_"+path_name+"_"+str(num_features)+".csv", header=True)
            else:
                df_result.to_csv("results_"+path_name+"_"+str(num_features)+".csv", header=True)

DF with Feature Importance
Sample features number: 6


PS16K  PS8K  PS1K  PS4K  HAVE_REPLICATION  HAVE_HASH
0       0     0     1     0                 0          0
1       0     0     0     1                 1          1
2       0     1     0     0                 1          1
3       0     0     1     0                 0          0
4       0     1     0     0                 1          1
5       0     1     0     0                 1          1
6       1     0     0     0                 0          1
7       1     0     0     0                 1          1
8       1     0     0     0                 1          1
9       0     0     1     0                 1          1
10      0     0     0     1                 1          1
11      0     0     0     1                 1          1
12      0     0     0     1                 0          1
13      0     0     0     1                 1          1
14      0     0     0     1                 1          1

[[1 0 0 0 0 0 0 0 1 1 0 0 0 0 1 1 0 0 0]
 [1 1 1 1 0 0 0 0 1 0 1 0 0 0 1 0 1 0 0]
 [1 1 1 1 1 1 1 1 1 0 0 1 0 0 1 0 0 1 0]
 [1 1 1 1 1 1 1 1 1 0 0 0 1 0 1 0 0 1 0]
 [1 1 1 1 1 1 0 0 1 0 0 1 0 0 1 1 0 0 0]
 [1 1 1 1 1 1 1 1 1 0 1 0 0 0 1 1 0 0 0]
 [1 1 1 1 0 0 0 0 1 0 1 0 0 0 1 0 0 0 1]
 [1 1 1 1 1 1 0 1 1 0 0 1 0 0 1 0 1 0 0]
 [1 1 1 1 1 1 0 1 1 0 0 0 1 0 1 0 1 0 0]
 [1 1 1 1 0 0 0 0 1 0 1 0 0 0 1 0 0 1 0]
 [1 1 1 0 0 0 0 0 1 0 1 0 0 0 1 0 1 0 0]
 [1 0 0 0 0 0 0 0 1 1 0 0 0 0 1 0 1 0 0]
 [1 1 1 0 0 0 0 0 1 0 0 0 1 0 1 0 1 0 0]]
[ 0.50289633  5.8277259  10.92846305 21.1979781  10.91825516  5.84551713
  5.83934279 10.90606135 21.24882514  5.83792136  5.82201462  0.5044075
 21.25651895]
It doesn't scale
[[1 1 1 1 0 0 0 0 1 0 1 0 0 0 1 0 1 0 0]
 [1 1 1 1 1 1 1 1 1 0 0 1 0 0 1 0 0 1 0]
 [1 1 1 1 1 1 1 1 1 0 0 0 1 0 1 0 0 1 0]
 [1 1 1 1 1 1 0 0 1 0 0 1 0 0 1 1 0 0 0]
 [1 1 1 1 1 1 1 1 1 0 1 0 0 0 1 1 0 0 0]
 [1 1 1 1 0 0 0 0 1 0 1 0 0 0 1 0 0 0 1]
 [1 1 1 1 1 1 0 1 1 0 0 1 0 0 1 0 1 0 0]
 [1

It doesn't scale
[[1 0 1 0 1 0 1 0 1 0 1 1 0 1 0 1 1 0 1 0 0 1 1 0 1 1 0 1 1 0 1 0 1 0]
 [1 0 1 0 1 0 1 0 1 0 1 0 1 0 1 1 1 0 0 1 1 0 1 0 1 1 0 1 1 0 1 0 1 0]
 [1 0 1 0 1 0 1 1 0 1 0 1 0 1 0 1 1 0 0 1 1 0 1 0 1 1 1 0 1 0 1 0 0 1]
 [1 0 1 0 1 0 1 0 1 0 1 1 0 0 1 1 1 0 1 0 0 1 1 0 1 1 1 0 0 1 1 0 1 0]
 [1 0 1 0 1 0 1 0 1 0 1 1 0 0 1 1 1 0 1 0 1 0 0 1 1 1 1 0 0 1 1 0 1 0]
 [1 0 1 0 1 0 1 1 0 1 0 1 0 1 0 1 1 0 0 1 1 0 1 0 1 1 1 0 1 0 0 1 1 0]
 [1 0 1 0 1 1 0 1 0 1 0 1 0 1 0 1 1 0 0 1 1 0 1 0 1 1 1 0 0 1 1 0 1 0]
 [1 1 0 1 0 1 0 1 0 1 0 1 0 1 0 1 0 1 1 0 1 0 1 0 1 1 1 0 0 1 1 0 1 0]
 [1 0 1 0 1 1 0 1 0 1 0 1 0 1 0 1 1 0 1 0 1 0 0 1 1 1 1 0 0 1 1 0 1 0]]
[10.91825516  5.84551713  5.83934279 10.90606135 21.24882514  5.83792136
  5.82201462  0.5044075  21.25651895]
It doesn't scale
[[1 0 1 0 1 0 1 1 0 1 0 1 0 1 0 1 1 0 0 1 1 0 1 0 1 1 1 0 1 0 1 0 0 1]
 [1 0 1 0 1 0 1 0 1 0 1 1 0 0 1 1 1 0 1 0 0 1 1 0 1 1 1 0 0 1 1 0 1 0]
 [1 0 1 0 1 0 1 0 1 0 1 1 0 0 1 1 1 0 1 0 1 0 0 1 1 1 1 0 0 1 1 0 1 0]
 [

algorithm_name  ft_dummyfication origin_ft_selection  \
0        LinearRegression             False                None   
1                   Lasso             False                None   
2                   Ridge             False                None   
3              ElasticNet             False                None   
4        LinearRegression             False                None   
..                    ...               ...                 ...   
157      LinearRegression              True        RandomForest   
158                 Lasso              True        RandomForest   
159                 Ridge              True        RandomForest   
160            ElasticNet              True        RandomForest   
161  PolynomialRegression              True        RandomForest   

                                          ft_selection  \
0    Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
1    Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
2    Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
3    Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
4    Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
..                                                 ...   
157  Index(['PS16K_0', 'PS16K_1', 'PS8K_0', 'PS8K_1...   
158  Index(['PS16K_0', 'PS16K_1', 'PS8K_0', 'PS8K_1...   
159  Index(['PS16K_0', 'PS16K_1', 'PS8K_0', 'PS8K_1...   
160  Index(['PS16K_0', 'PS16K_1', 'PS8K_0', 'PS8K_1...   
161  Index(['PS16K_0', 'PS16K_1', 'PS8K_0', 'PS8K_1...   

                                       hyperparameters  size_target  \
0                                   LinearRegression()  Performance   
1                      Lasso(alpha=0.01, max_iter=100)  Performance   
2                                    Ridge(alpha=0.01)  Performance   
3    ElasticNet(alpha=0.01, l1_ratio=1.0, max_iter=...  Performance   
4                                   LinearRegression()  Performance   
..                                                 ...          ...   
157                                 LinearRegression()  Performance   
158                        Lasso(alpha=25, max_iter=1)  Performance   
159                                    Ridge(alpha=25)  Performance   
160     ElasticNet(alpha=25, l1_ratio=0.0, max_iter=1)  Performance   
161                                 LinearRegression()  Performance   

     test_size                                         coef_order  \
0          0.1  PS16K               9.793024e+00
PS4K         ...   
1          0.1  PS16K            1.032722e+01
HAVE_CRYPTO     ...   
2          0.1  PS16K               9.741295
PS4K             ...   
3          0.1  PS16K            1.032722e+01
HAVE_CRYPTO     ...   
4          0.2  PS16K               9.797404e+00
PS4K         ...   
..         ...                                                ...   
157        0.9                         Series([], dtype: float64)   
158        0.9                         Series([], dtype: float64)   
159        0.9                         Series([], dtype: float64)   
160        0.9                         Series([], dtype: float64)   
161        0.9                         Series([], dtype: float64)   

                                              accuracy  
0    count      2.000000
mean     137.785440
std   ...  
1    count      2.000000
mean     205.468593
std   ...  
2    count      2.000000
mean     139.526907
std   ...  
3    count      2.000000
mean     205.468593
std   ...  
4    count      3.000000
mean      96.845568
std   ...  
..                                                 ...  
157  count      14.000000
mean      788.233548
std ...  
158  count      14.000000
mean      788.233548
std ...  
159  count      14.000000
mean      788.233548
std ...  
160  count      14.000000
mean      788.233548
std ...  
161  count      14.000000
mean      788.233548
std ...  

[162 rows x 9 columns]

...

It doesn't scale
[[1 1 0 ... 0 1 0]
 [1 0 1 ... 0 1 0]
 [1 0 1 ... 0 1 0]
 ...
 [1 1 0 ... 1 1 0]
 [1 0 1 ... 1 1 0]
 [1 0 1 ... 1 1 0]]
[ 0.63121636 10.75294845 19.97858892  0.46042144  0.53931953  6.52869677
 19.98236192  0.44549082  2.38763377  0.46276037  0.6336659   0.53556544
  0.56723144  1.30443723  0.4532531   0.63790528  0.50878492  0.52050541
  0.50574528  0.63955232  2.13844142  0.50421374  0.46032041  0.58125479
  0.51781405 19.96464238 39.0335925   0.58230623 37.76111226 19.97460374
  0.92122011  0.51007441  0.64569831  0.44551869  0.50964341  0.51477772
  0.36762328 37.79094682  0.36514846  6.52165923 19.95865126  1.25427547
  0.63255408  1.30660997  0.50029536  0.48383318  0.44827197  2.02675256
  0.63340469  0.50593092  0.36812949  0.51718221  6.51510303  1.26100805
  3.23904654  0.51302426  0.35959828  0.46455982 20.02572924  1.25421623
  0.51364254  1.30697674  1.25373614  0.51643662  0.94471613  0.63781241
  0.61814546  0.36208764  0.63548708  5.83938618  0.65150856

It doesn't scale
[[1 1 0 ... 0 0 1]
 [1 0 1 ... 1 1 0]
 [1 1 0 ... 1 1 0]
 ...
 [1 1 0 ... 1 1 0]
 [1 0 1 ... 1 1 0]
 [1 0 1 ... 1 1 0]]
[ 0.43429821  3.22911303  0.46645749  1.24142603 37.65053526  0.52881862
 20.00845023  0.52792203  0.50154721  0.64465567 37.81359595  6.51411364
  0.64127913  0.46382577  0.44426082  1.25339253  0.63071577  0.45198705
  0.4997251   1.25254311  6.53443477  0.63172487 37.74742382  0.95021056
 20.00143346  0.92977969  0.51724438  0.75026649  0.47135008  1.30764697
  0.3657899   1.24749946  0.91891992  1.2566481   0.64336597  0.48508726
  0.48593918  0.50065321  0.93331645  0.63522772  0.569552    1.25774458
  0.45437987 10.74228897  0.64120082  0.51661213  0.92954792  0.92539686
  0.62697118  0.74348166  0.63198292  0.51110989  2.37463564 20.00142997
  0.51167632  0.44917654  0.63563923  6.52784772  0.50224228 10.75622641
  0.54045556  0.46197044  6.50772074 20.02159232  3.20123444  0.94388721
  0.45445538  0.92128526  0.94734859 19.99529554  0.94375349

[[1 0 1 ... 0 1 0]
 [0 1 1 ... 0 1 0]
 [0 1 1 ... 0 1 0]
 ...
 [1 0 1 ... 0 1 0]
 [0 1 1 ... 0 0 1]
 [0 1 1 ... 0 1 0]]
[ 0.63121636 10.75294845 19.97858892  0.46042144  0.53931953  6.52869677
 19.98236192  0.44549082  2.38763377  0.46276037  0.6336659   0.53556544
  0.56723144  1.30443723  0.4532531   0.63790528  0.50878492  0.52050541
  0.50574528  0.63955232  2.13844142  0.50421374  0.46032041  0.58125479
  0.51781405 19.96464238 39.0335925   0.58230623 37.76111226 19.97460374
  0.92122011  0.51007441  0.64569831  0.44551869  0.50964341  0.51477772
  0.36762328 37.79094682  0.36514846  6.52165923 19.95865126  1.25427547
  0.63255408  1.30660997  0.50029536  0.48383318  0.44827197  2.02675256
  0.63340469  0.50593092  0.36812949  0.51718221  6.51510303  1.26100805
  3.23904654  0.51302426  0.35959828  0.46455982 20.02572924  1.25421623
  0.51364254  1.30697674  1.25373614  0.51643662  0.94471613  0.63781241
  0.61814546  0.36208764  0.63548708  5.83938618  0.65150856  0.91835068
  0.

[[1 0 1 ... 0 0 1]
 [0 1 1 ... 1 1 0]
 [1 0 1 ... 0 0 1]
 ...
 [1 0 1 ... 0 1 0]
 [0 1 1 ... 0 0 1]
 [0 1 1 ... 0 1 0]]
[ 0.43429821  3.22911303  0.46645749  1.24142603 37.65053526  0.52881862
 20.00845023  0.52792203  0.50154721  0.64465567 37.81359595  6.51411364
  0.64127913  0.46382577  0.44426082  1.25339253  0.63071577  0.45198705
  0.4997251   1.25254311  6.53443477  0.63172487 37.74742382  0.95021056
 20.00143346  0.92977969  0.51724438  0.75026649  0.47135008  1.30764697
  0.3657899   1.24749946  0.91891992  1.2566481   0.64336597  0.48508726
  0.48593918  0.50065321  0.93331645  0.63522772  0.569552    1.25774458
  0.45437987 10.74228897  0.64120082  0.51661213  0.92954792  0.92539686
  0.62697118  0.74348166  0.63198292  0.51110989  2.37463564 20.00142997
  0.51167632  0.44917654  0.63563923  6.52784772  0.50224228 10.75622641
  0.54045556  0.46197044  6.50772074 20.02159232  3.20123444  0.94388721
  0.45445538  0.92128526  0.94734859 19.99529554  0.94375349 20.01780249
  0.

algorithm_name  ft_dummyfication origin_ft_selection  \
0          LinearRegression             False                None   
1                     Lasso             False                None   
2                     Ridge             False                None   
3                ElasticNet             False                None   
4          LinearRegression             False                None   
...                     ...               ...                 ...   
11659      LinearRegression              True        RandomForest   
11660                 Lasso              True        RandomForest   
11661                 Ridge              True        RandomForest   
11662            ElasticNet              True        RandomForest   
11663  PolynomialRegression              True        RandomForest   

                                            ft_selection  \
0      Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
1      Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
2      Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
3      Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
4      Index(['root', 'HAVE_CRYPTO', 'HAVE_HASH', 'HA...   
...                                                  ...   
11659  Index(['HAVE_CRYPTO_0', 'HAVE_CRYPTO_1', 'PS32...   
11660  Index(['HAVE_CRYPTO_0', 'HAVE_CRYPTO_1', 'PS32...   
11661  Index(['HAVE_CRYPTO_0', 'HAVE_CRYPTO_1', 'PS32...   
11662  Index(['HAVE_CRYPTO_0', 'HAVE_CRYPTO_1', 'PS32...   
11663  Index(['HAVE_CRYPTO_0', 'HAVE_CRYPTO_1', 'PS32...   

                                         hyperparameters  size_target  \
0                                     LinearRegression()  Performance   
1                        Lasso(alpha=0.01, max_iter=100)  Performance   
2                                      Ridge(alpha=0.01)  Performance   
3      ElasticNet(alpha=0.01, l1_ratio=1.0, max_iter=...  Performance   
4                                     LinearRegression()  Performance   
...                                                  ...          ...   
11659                                 LinearRegression()  Performance   
11660                       Lasso(alpha=0.1, max_iter=5)  Performance   
11661                                   Ridge(alpha=0.8)  Performance   
11662                 ElasticNet(alpha=0.05, max_iter=5)  Performance   
11663                                 LinearRegression()  Performance   

       test_size                                         coef_order  \
0            0.1  PS16K               9.793024e+00
PS4K         ...   
1            0.1  PS16K            1.032722e+01
HAVE_CRYPTO     ...   
2            0.1  PS16K               9.741295
PS4K             ...   
3            0.1  PS16K            1.032722e+01
HAVE_CRYPTO     ...   
4            0.2  PS16K               9.797404e+00
PS4K         ...   
...          ...                                                ...   
11659        0.9  HAVE_CRYPTO_0    6.352278
HAVE_CRYPTO_1    6.3...   
11660        0.9  HAVE_CRYPTO_0    1.172922e+01
PS16K_0         ...   
11661        0.9  HAVE_CRYPTO_0    5.888844
HAVE_CRYPTO_1    5.8...   
11662        0.9  HAVE_CRYPTO_0    8.327032
HAVE_CRYPTO_1    3.5...   
11663        0.9  PS32K_0          1.060340e+14
HAVE_CRYPTO_0   ...   

                                                accuracy  
0      count      2.000000
mean     137.785440
std   ...  
1      count      2.000000
mean     205.468593
std   ...  
2      count      2.000000
mean     139.526907
std   ...  
3      count      2.000000
mean     205.468593
std   ...  
4      count      3.000000
mean      96.845568
std   ...  
...                                                  ...  
11659  count     309.000000
mean      441.147735
std ...  
11660  count     309.000000
mean      353.752464
std ...  
11661  count     309.000000
mean      379.428521
std ...  
11662  count     309.000000
mean      379.633949
std ...  
11663  count    3.090000e+02
mean     2.169359e+14
st...  

[11664 rows x 9 columns]

In [ ]:
len(x_train)

In [ ]:
df_result['accuracy'][0]

import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd

rs = []
for i in range(len(df_result['accuracy'])):
    rs.append(df_result['accuracy'][i]['mean'])

# rs
# display (df_result['algorithm_name'], df_result['accuracy'], rs)

plt.scatter(df_result['algorithm_name'], rs, color ="blue", marker = "s")
plt.plot(df_result['algorithm_name'], rs, color ="blue")


In [ ]:
# Boxplot
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd


data = [model['LinearRegression'].coef_, model['Lasso'].coef_, model['Ridge'].coef_, model['ElasticNet'].coef_, model['PolynomialRegression'].coef_]
fig1, ax1 = plt.subplots()
ax1.set_title('Coeficient of feature importance for all algorithms')
ax1.boxplot(data)
plt.show()